In [1]:
import geopandas as gpd
import osmnx as ox
import xgboost as xgb
import pickle
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestRegressor,GradientBoostingRegressor
import time 
import warnings
import time
import pandas as pd
import matplotlib.pyplot as plt

C:\Users\Diametrix\anaconda3\lib\site-packages\numpy\_distributor_init.py:30: UserWarning: loaded more than 1 DLL from .libs:
C:\Users\Diametrix\anaconda3\lib\site-packages\numpy\.libs\libopenblas.FB5AE2TYXYH2IJRDKGDGQ3XBKLKTF43H.gfortran-win_amd64.dll
C:\Users\Diametrix\anaconda3\lib\site-packages\numpy\.libs\libopenblas.GK7GX5KEQ4F6UYO3P26ULGBQYHGQO7J4.gfortran-win_amd64.dll
  warnings.warn("loaded more than 1 DLL from .libs:"
C:\Users\Diametrix\AppData\Roaming\Python\Python39\site-packages\geopandas\_compat.py:124: UserWarning: The Shapely GEOS version (3.11.1-CAPI-1.17.1) is incompatible with the GEOS version PyGEOS was compiled with (3.10.4-CAPI-1.16.2). Conversions between both will be slow.
  warnings.warn(
C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\2103913301.py:1: DeprecationWarning: Shapely 2.0 is installed, but because PyGEOS is also installed, GeoPandas still uses PyGEOS by default. However, starting with version 0.14, the default will switch to Shapely. To force

In [9]:
pd.set_option('display.max_columns', None)
a.shape

(11231, 47)

In [8]:
#path to read the building files
path=r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\osm filtre\batiment"

#list of deprtmenet in France
list_departement=pd.read_excel(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\\Liste-Excel-des-departements-francais.xlsx")
list_departement.head(2)

N° Département        Chef-lieu                Région
0  01         Ain  Bourg-en-Bresse  Auvergne-Rhône-Alpes
1  02       Aisne             Laon       Hauts-de-France

In [42]:
#Data of each IRIS : POP ...
iris_data=pd.read_excel("Y:\REFERENTIEL DATA\RP 2022 FRANCE\GEODATA - IRIS\Geodata_IRIS_essentiels.xlsx")

#geoemtry of each IRIS
contour_iris=gpd.read_file(r'Y:\REFERENTIEL DATA\RP 2022 FRANCE\CARTOGRAPHIE\Cartographie_France_IRIS_2019\CONTOURS-IRIS_2-1_SHP_LAMB93_FXX-2019\CONTOURS-IRIS.shp').to_crs('EPSG:3857')

In [87]:
#les villes choisi : villes populé
villes=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\villes\\villes.pkl","rb"))
villes.head(2)

0   P17_POP
INSEE_COM                                                             
03310      POLYGON ((733837.800 6557158.000, 733810.300 6...   45327.0
06004      POLYGON ((1030984.700 6283249.900, 1030947.300...  397004.0

In [ ]:
#batiments sans nombre d'étage
building_no_na=[]

#les iris qui sont à coté du batiments
all_nearby_buildings={}

#indice(position) du iris de chaque batiment
iris_building_id=[]

#tout les batiments
all_building=[]

for i ,row in list_departement.iterrows():
    try:
            
        contour_iris_dep=contour_iris
        
        #les batiments du département
        building=pd.read_pickle(path+r"\\"+row["Département"].lower()+"_buildings.pkl").to_crs('EPSG:3857')
        
        #get only the buildings with no Nan values
        building_no=building[~building['building:levels'].isna()]
        print(row["Département"].lower())
        print(building_no.shape)
        
        #append lists
        all_building.append(building)
        building_no_na.append(building_no)
        
        #get the iris of each building
        iris_buildings=gpd.sjoin(building,contour_iris_dep,predicate="intersects",how="left")
        iris_buildings = iris_buildings[~iris_buildings.index.duplicated(keep='first')].reset_index()
        
        #ici pour enregistrer les iris des batiments
        iris_building_id.append(iris_buildings[["index_right",'element_type',"osmid"]].set_index(['element_type',"osmid"]))
       
    
        iris_buildings=gpd.GeoDataFrame(
        iris_buildings[['element_type',"osmid","CODE_IRIS"]].merge(contour_iris_dep[['CODE_IRIS',"geometry"]]),

        ).set_geometry("geometry").set_crs('EPSG:3857')
        
        
     
        #get the iris that touches each other
        xx=gpd.sjoin(iris_buildings,contour_iris_dep,predicate="touches")
        nearby_buildings=xx[["osmid",'element_type',"CODE_IRIS_left","index_right"]].groupby(["element_type",'osmid'])['index_right'].apply(list)
        
        #nearby_buildings contains {"building _id": list of nearby iris}
        nearby_buildings=nearby_buildings.to_dict()
        all_nearby_buildings.update(nearby_buildings)
   
    except:
        
        pass


In [9]:
#list to pandas dataframe
all_building=pd.concat(all_building) 
iris_building_id=pd.concat(iris_building_id)
building_no_na=pd.concat(building_no_na)
iris_building_id=iris_building_id.reset_index().set_index(["element_type" ,"osmid","index_right"])

In [2]:
#load saved data
all_building=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\osm filtre\\all_buildings.pkl","rb"))
all_nearby_buildings=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\osm filtre\\all_nearby_buildings.pkl","rb"))
iris_building_id=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\osm filtre\\iris_building_id.pkl","rb"))
building_no_na=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\osm filtre\\building_no_na.pkl",'rb'))

In [3]:
building_no_na.shape

(231328, 10)

In [12]:
#all building and building_no_na have the same structure
all_building.head(2)

geometry  \
element_type osmid                                                         
way          78149618  POLYGON ((552043.251 5752882.138, 552043.674 5...   
             78149619  POLYGON ((553499.210 5752608.145, 553498.798 5...   

                      building shop building:levels amenity name addr:street  \
element_type osmid                                                             
way          78149618      yes  NaN             1.0     NaN  NaN         NaN   
             78149619      yes  NaN             1.0     NaN  NaN         NaN   

                      addr:city addr:housenumber addr:postcode  
element_type osmid                                              
way          78149618       NaN              NaN           NaN  
             78149619       NaN              NaN           NaN

In [13]:
#building_id:list of nearby iris 
all_nearby_buildings

{('relation', 1183522): [12629, 24324, 18338],
 ('relation', 1183523): [12629, 24324, 29179, 44350, 9329, 3325, 477, 4611],
 ('relation', 1183524): [12629, 24324, 29179, 44350, 9329, 3325, 477, 4611],
 ('relation', 2067205): [26356, 7877, 26667, 42257, 22866],
 ('way', 78149618): [12629, 24324, 18338],
 ('way', 78149619): [12629, 24324, 18338],
 ('way', 78149620): [12629, 24324, 29179, 44350, 9329, 3325, 477, 4611],
 ('way', 78149621): [12629, 24324, 18338],
 ('way', 78149636): [12629, 24324, 29179, 44350, 9329, 3325, 477, 4611],
 ('way', 78149639): [12629, 24324, 29179, 44350, 9329, 3325, 477, 4611],
 ('way', 78149641): [12629, 24324, 18338],
 ('way', 78149648): [12629, 24324, 29179, 44350, 9329, 3325, 477, 4611],
 ('way', 78149650): [12629, 24324, 29179, 44350, 9329, 3325, 477, 4611],
 ('way', 78149652): [24324, 18338, 9329, 3325, 39902, 39273, 48263],
 ('way', 78149654): [24324, 18338, 9329, 3325, 39902, 39273, 48263],
 ('way', 78149658): [12629, 24324, 29179, 44350, 9329, 3325, 477

In [14]:
#les indices des batiments dont on connait leurs IRIS voisins
keys_nearby_buildings=all_nearby_buildings.keys()
iris_data=iris_data.set_index("CODE_IRIS")
#les indices (positions) de tout les batiments
all_indices=[i for i in range(len(all_building))]

# ML

In [13]:
def f (x):
    
    #si x is None on retourne -100
    if x is None or x!=x:
        return -100
    else:
        if type(x)==str and x.isnumeric():
            return float(x)
            
        try:
            
            #si x est de forme 1;2;3  on retourne 1#sinon on retoune x
            if type(x) !=  np.int64 and  type(x) !=  np.int32 and type(x) !=int and type(x)!=float:
                
                return float(x.split(';')[0])
            
            else:
                return float(x)
        except:#si x est par example une lettre (cas priculiers ) on retourne 1
            return 1
         

In [16]:
print("Pour ",None, " : ",f(None) )
print("Pour ","10;2;3", " : ",f("10;2;3") )
print("Pour ",2.0, " : ",f(2.0) )
print("Pour ","2.0", " : ",f("2.0") )
print("Pour ","-1", " : ",f("-1") )
print("Pour ",-1, " : ",f(-1) )
print("Pour ","q", " : ",f("q") )

Pour  None  :  -100
Pour  10;2;3  :  10.0
Pour  2.0  :  2.0
Pour  2.0  :  2.0
Pour  -1  :  -1.0
Pour  -1  :  -1.0
Pour  q  :  1


In [84]:
warnings.filterwarnings("ignore")
#Initialisation
data=None #données
j=0#indices
k=10 #nombre des voisins
y_true=[]# nb levels . à utiliser dans le modéle 
start=time.time()


print('number of rows :'+str(len(building_no_na)))

for i ,row in building_no_na.iterrows():
    
    if j%1000==0:
        print(time.time()-start)
        start=time.time()
    
    y_true.append(row['building:levels'])
    
    #si on sait le les iris visins du batiment ayant l'indice 'i' (il suffit de verfifier que i est dans keys_nearby_buildings)
    #alors 
    if i in  keys_nearby_buildings and all_nearby_buildings[i][0] is not None:
        #index (position) of the iris of the current building
        current_iris_index=iris_building_id.at[i[0],i[1]].index[0]
        
        #position of all the iris nearby
        iris_ids=list(all_nearby_buildings[i])
        iris_ids.append(current_iris_index)
        
        #get all the indices of the buidlings in the nearby iris and the iris where the building is  
        mask=np.isin(np.array(iris_building_id.index.get_level_values("index_right")),iris_ids)
        indices=np.where(mask)[0]
    else:# si on ne sait pas les iris voisins du batiments (des erreurs dans le code qui calcule all_nearby_buildings).
        #Pas grave . y en 'a pas beaucoup
        print('####################################')
        indices=all_indices
        
    #on prend les batiments qui sont dans l'iris ou(where) il ya le batiment et les iris voisins
    buildings_in_iris=all_building.iloc[indices]

    #on calcule la distance entre le batiments et tout les autres batments à coté
    distance=buildings_in_iris.distance(row['geometry']).sort_values()
    
    #remove the current building from the distance dataframe (distance will be 0 ofc)
    distance=distance.drop(i)

    #take the k nearest neighboors
    a=buildings_in_iris.loc[distance.index].iloc[:k]
    
    #Information about the nearby buildings
    areas=a.area.to_numpy() 
    distances=distance.iloc[:k].to_numpy()
    types=a['building'].to_numpy()
    levels=np.vectorize (f )(a['building:levels'].to_numpy())
    
    #information about the iris
    iris=contour_iris.iloc[current_iris_index]
    if iris['TYP_IRIS'] ==iris['TYP_IRIS']:
        iris_type=np.array([iris['TYP_IRIS']])
    else:
        iris_type=None
    iris_area=np.array([iris['geometry'].area])
    
    #information about the building itself
    type_building=np.array([row['building']])
    area_building=np.array([row['geometry'].area])
    
    #densité de l'iris
    area=iris["geometry"].area/10**6
    iris=iris_data.loc[iris["CODE_IRIS"]]
    pop=iris['P17_POP']
    densite=[pop/area]

    if data is None:
        
        data=np.concatenate([type_building,area_building,iris_type,iris_area,densite,areas,types,levels,distances])
    else:
        
        data=np.vstack([data,np.concatenate([type_building,area_building,iris_type,iris_area,densite,areas,types,levels,distances])])
    

    
     
    j+=1
    


number of rows :231328
6.045943975448608
201.17363929748535
196.66942524909973
223.91012740135193
184.54901552200317
199.374507188797
198.93171787261963
201.63251423835754
####################################
####################################
####################################
419.0562496185303
197.91812539100647
202.18882179260254
197.38167643547058
230.97140216827393
222.25416946411133
206.6891701221466
206.532972574234
201.0262634754181
210.71679067611694
198.9076647758484
228.1717221736908
217.35397815704346
232.7627248764038
228.77924489974976
250.91820859909058
254.49614071846008
237.1983516216278
257.95234513282776
251.29999780654907
233.92519116401672
243.70984768867493
249.92696499824524
235.81962418556213
228.4407525062561
230.79045295715332
226.5147271156311
227.89342856407166
239.93165731430054
234.7304244041443
226.54512238502502
218.1334626674652
221.91035437583923
219.11851406097412
214.09044742584229
219.2118046283722
215.41370010375977
208.99850249290466
222.23570

In [24]:
k=10
y_true=building_no_na['building:levels'].values
#pickle.dump(data,open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\\donnée_prediction_levels.pkl","wb"))
data=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\\données modele\\donnée_prediction_levels.pkl","rb"))
data.shape

(231328, 45)

In [29]:
data_no[["type_building" ,"area_building" ,"iris_type" ,"iris_area" ,"iris_densite","areas0","distances0","types0","levels0"]]

type_building area_building iris_type        iris_area iris_densite  \
0           detached   1145.431438         H  39045056.799018    80.011647   
1                yes   1811.609451         H    8950243.60309   293.177979   
2           detached     77.012978         H  39045056.799018    80.011647   
3                yes    434.974262         H   2432227.761646  1732.948881   
4         apartments    359.782967         H   2432227.761646  1732.948881   
...              ...           ...       ...              ...          ...   
231323           yes   1046.704411         H    322324.462012  6125.709405   
231324           yes    772.237487         H   1847028.597088  1433.815749   
231325           yes    212.680191         H   1847028.597088  1433.815749   
231326           yes    245.107214         H    464632.465989  6653.976241   
231327           yes   2090.122514         H    315914.308555  5855.259722   

             areas0 distances0    types0 levels0  
0         77.012978        0.0  detached     2.0  
1        131.654501   4.601732       yes     2.0  
2       1145.431438        0.0  detached     2.0  
3         81.014063  10.126972       yes     2.0  
4        319.626627  13.869996       yes     2.0  
...             ...        ...       ...     ...  
231323   719.125916        0.0       yes     6.0  
231324   125.985687        0.0       yes     2.0  
231325   145.247218        0.0       yes     2.0  
231326   624.864219        0.0       yes     1.0  
231327    41.962178  19.535735       yes     1.0  

[231328 rows x 9 columns]

In [31]:
(data_no['levels0']==-100).sum()

0

In [26]:
#create a dataframe
columns=["type_building","area_building","iris_type","iris_area","iris_densite"]
for j in ["areas","types","levels","distances"]:
    for i in range(k):
        columns.append(j+str(i))

data_no=pd.DataFrame(data,columns=columns)
data_no.head()

type_building area_building iris_type        iris_area iris_densite  \
0      detached   1145.431438         H  39045056.799018    80.011647   
1           yes   1811.609451         H    8950243.60309   293.177979   
2      detached     77.012978         H  39045056.799018    80.011647   
3           yes    434.974262         H   2432227.761646  1732.948881   
4    apartments    359.782967         H   2432227.761646  1732.948881   

        areas0        areas1       areas2      areas3      areas4  ...  \
0    77.012978  77487.467692  1336.929794  222.438374  751.650926  ...   
1   131.654501    308.911291    201.73839   99.077167   261.32173  ...   
2  1145.431438  77487.467692  1336.929794  222.438374  751.650926  ...   
3    81.014063    531.316705   225.150437  126.086577    37.61948  ...   
4   319.626627    5119.66271     97.76897  298.528899  501.041235  ...   

  distances0  distances1  distances2  distances3  distances4  distances5  \
0        0.0  234.005508   283.34692  335.731341  447.418368  481.574988   
1   4.601732   14.465082   14.563975   15.007751    16.79121    21.52599   
2        0.0  255.725996  285.468083  337.595595  461.339317  513.757788   
3  10.126972   17.315202   18.101702   24.028222   26.539052   26.680237   
4  13.869996   37.049677   38.725885   41.643799   44.692879   47.993069   

   distances6  distances7  distances8  distances9  
0  485.396616  511.874534   517.19872  533.984768  
1   27.261808   28.056698   28.699393   32.182955  
2  516.621466  542.479292  549.290071   563.47553  
3   26.985377   30.082018     32.4264   40.343866  
4   56.980109   59.080613   66.077812   69.824248  

[5 rows x 45 columns]

In [23]:
data_no

type_building  area_building  iris_type     iris_area  iris_densite  \
0                  34    1145.431396          2  3.904506e+07     80.011650   
1                 130    1811.609497          2  8.950244e+06    293.177979   
2                  34      77.012978          2  3.904506e+07     80.011650   
3                 130     434.974274          2  2.432228e+06   1732.948853   
4                   4     359.782959          2  2.432228e+06   1732.948853   
...               ...            ...        ...           ...           ...   
231323            130    1046.704468          2  3.223245e+05   6125.709473   
231324            130     772.237488          2  1.847029e+06   1433.815796   
231325            130     212.680191          2  1.847029e+06   1433.815796   
231326            130     245.107208          2  4.646325e+05   6653.976074   
231327            130    2090.122559          2  3.159143e+05   5855.259766   

             areas0        areas1       areas2       areas3       areas4  ...  \
0         77.012978  77487.468750  1336.929810   222.438370   751.650940  ...   
1        131.654495    308.911285   201.738388    99.077164   261.321716  ...   
2       1145.431396  77487.468750  1336.929810   222.438370   751.650940  ...   
3         81.014061    531.316711   225.150436   126.086578    37.619480  ...   
4        319.626617   5119.662598    97.768967   298.528900   501.041229  ...   
...             ...           ...          ...          ...          ...  ...   
231323   719.125916   2555.890381    58.874794  1790.764160  1245.451294  ...   
231324   125.985687    722.249451   509.830170    69.602966    74.143547  ...   
231325   145.247223    167.096100   182.686829   280.296692   170.433472  ...   
231326   624.864197   1190.963379  1180.851074   483.992920   497.279236  ...   
231327    41.962177   3634.666504  1214.785034  5119.627930   192.223953  ...   

        distances0  distances1  distances2  distances3  distances4  \
0         0.000000  234.005508  283.346924  335.731354  447.418365   
1         4.601732   14.465081   14.563974   15.007751   16.791210   
2         0.000000  255.725998  285.468079  337.595581  461.339325   
3        10.126972   17.315203   18.101702   24.028221   26.539051   
4        13.869996   37.049675   38.725883   41.643799   44.692879   
...            ...         ...         ...         ...         ...   
231323    0.000000   16.463680   29.453564   42.758686   46.606079   
231324    0.000000    7.347605   16.330507   21.049896   21.234665   
231325    0.000000   11.567378   20.092806   33.561962   35.011616   
231326    0.000000   24.141106   25.091621   33.861370   44.514961   
231327   19.535734   22.074306   22.366274   32.805038   33.504086   

        distances5  distances6  distances7  distances8  distances9  
0       481.574982  485.396606  511.874542  517.198730  533.984741  
1        21.525990   27.261808   28.056698   28.699394   32.182957  
2       513.757812  516.621460  542.479309  549.290100  563.475525  
3        26.680237   26.985376   30.082018   32.426399   40.343864  
4        47.993069   56.980110   59.080612   66.077812   69.824249  
...            ...         ...         ...         ...         ...  
231323   48.450428  105.467773  114.557259  118.224419  120.359772  
231324   22.434971   23.895140   28.169863   28.885075   29.514271  
231325   35.515221   36.931866   37.673466   41.588253   43.992996  
231326   52.180370   74.399696   82.425133   82.897484   84.401466  
231327   34.757332   36.823944   37.139511   37.369656   38.715096  

[231328 rows x 45 columns]

In [14]:
#building_level is the true label Y
building_level=np.array([f(i) for i in y_true])
building_level.shape

(231328,)

In [15]:
pd.Series(building_level).value_counts()

 2.0     60980
 1.0     39791
 3.0     27794
 5.0     23483
 4.0     22463
 7.0     20944
 6.0     18263
 8.0      8054
 9.0      3311
 10.0     1756
 11.0     1158
 0.0       842
 12.0      524
 13.0      414
 16.0      262
 15.0      261
 14.0      232
 17.0      187
 18.0      180
 19.0      118
 20.0       66
 22.0       28
 21.0       22
 31.0       18
 32.0       15
-1.0        14
 27.0       14
 23.0       12
 25.0       12
 33.0       12
 24.0       11
 35.0       10
 36.0        9
 28.0        9
 30.0        8
 34.0        7
 40.0        6
 39.0        6
 29.0        5
 26.0        5
 37.0        4
-2.0         3
 42.0        2
 41.0        2
 38.0        2
 43.0        2
 55.0        1
 59.0        1
 44.0        1
 48.0        1
-5.0         1
 47.0        1
 49.0        1
dtype: int64

In [16]:
#convert columns from object to int
for c in data_no:
    if "area" in c or "levels" in c or "distances" in c or "iris_densite" in c:
        print(c)
        data_no[c]=data_no[c].astype(np.float32)

area_building
iris_area
iris_densite
areas0
areas1
areas2
areas3
areas4
areas5
areas6
areas7
areas8
areas9
levels0
levels1
levels2
levels3
levels4
levels5
levels6
levels7
levels8
levels9
distances0
distances1
distances2
distances3
distances4
distances5
distances6
distances7
distances8
distances9


In [17]:
#encoder les colonnes iris_type,type_building,et les types des batiments voisins.
list_encoders=[]
from sklearn.preprocessing import OrdinalEncoder
for c in data_no.columns:
    if data_no[c].dtype=="O":
        print(c)
        enc = OrdinalEncoder()
        data_no[c]=enc.fit_transform(data_no[c].to_numpy().reshape(-1,1) ).squeeze().astype(np.int)
        list_encoders.append(enc)
        

type_building
iris_type
types0


C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\4012039046.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  data_no[c]=enc.fit_transform(data_no[c].to_numpy().reshape(-1,1) ).squeeze().astype(np.int)
C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\4012039046.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision

types1
types2
types3


C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\4012039046.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  data_no[c]=enc.fit_transform(data_no[c].to_numpy().reshape(-1,1) ).squeeze().astype(np.int)
C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\4012039046.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision

types4
types5
types6


C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\4012039046.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  data_no[c]=enc.fit_transform(data_no[c].to_numpy().reshape(-1,1) ).squeeze().astype(np.int)
C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\4012039046.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision

types7
types8
types9


C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\4012039046.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  data_no[c]=enc.fit_transform(data_no[c].to_numpy().reshape(-1,1) ).squeeze().astype(np.int)
C:\Users\Diametrix\AppData\Local\Temp\ipykernel_25016\4012039046.py:8: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision

In [18]:
#train test split
X_train, X_test, y_train, y_test =train_test_split(data_no,building_level,random_state=123,test_size=0.2)

# DT

In [19]:
from sklearn.tree import DecisionTreeRegressor

In [20]:
model=DecisionTreeRegressor()

In [35]:
model.fit(X_train,y_train)

DecisionTreeRegressor()

In [37]:
ypred = dt.predict(X_test)
print('The error is :'+str(np.sum(np.abs(model.predict(X_test).round()-y_test))/len(y_test)))
print('Train error is :'+str(np.sum(np.abs(model.predict(X_train).round()-y_train))/len(y_train)))

print("Std train error:",np.std(np.abs(model.predict(X_train).round()-y_train)))
print("Std test error:",np.std(np.abs(model.predict(X_test).round()-y_test)))

print("Median Abs error ",np.median(np.abs(model.predict(X_test).round()-y_test)))

The error is :1.1776034236804565
Train error is :0.0
Std train error: 0.0
Std test error: 1.88630743059701
Median Abs error  1.0


#  Random forest

In [43]:
from  sklearn.ensemble import RandomForestClassifier
model=RandomForestClassifier()
model.fit(X_train,y_train)
ypred = dt.predict(X_test)
print('The error is :'+str(np.sum(np.abs(model.predict(X_test).round()-y_test))/len(y_test)))
print('Train error is :'+str(np.sum(np.abs(model.predict(X_train).round()-y_train))/len(y_train)))

print("Std train error:",np.std(np.abs(model.predict(X_train).round()-y_train)))
print("Std test error:",np.std(np.abs(model.predict(X_test).round()-y_test)))

print("Median Abs error ",np.median(np.abs(model.predict(X_test).round()-y_test)))

The error is :0.8407253706825747
Train error is :0.0
Std train error: 0.0
Std test error: 1.6173749223895588
Median Abs error  0.0


# XGBoost

In [38]:
dtrain = xgb.DMatrix(X_train, label=y_train)
dtest = xgb.DMatrix(X_test, label=y_test)

In [49]:

param = {'max_depth': 5, 'eta': 0.1, 'objective': 'reg:squarederror',"gamma":2,"lambda":4,"verbosity":0}

param['nthread'] = 4
param['eval_metric'] = ["mae"]
param['verbosity']=0
evallist = [(dtrain, 'train'), (dtest, 'eval')]
num_round = 500

In [50]:
start=time.time()
model = xgb.train(param, dtrain, num_round)

end=time.time()
ypred = model.predict(dtest)
print('The error is :'+str(np.sum(np.abs(model.predict(dtest).round()-y_test))/len(y_test)))
print('Train error is :'+str(np.sum(np.abs(model.predict(dtrain).round()-y_train))/len(y_train)))

print("Std train error:",np.std(np.abs(model.predict(dtrain).round()-y_train)))
print("Std test error:",np.std(np.abs(model.predict(dtest).round()-y_test)))

print("Median Abs error ",np.median(np.abs(model.predict(dtest).round()-y_test)))
print('Train time '+str(end-start))

The error is :0.7939739765702676
Train error is :0.7229415006862565
Std train error: 1.032203944796004
Std test error: 1.2763638748206956
Median Abs error  0.0
Train time 129.0147261619568


# Stats

In [95]:
intervals=[5,10,15,20]
ypred=model.predict(dtest)
for i,el in enumerate(intervals):
    
    if i ==0:
        a="0"
        b=str(el)
        mask=y_test<=el
    elif i ==len(intervals)-1:
        a="+infini"
        mask=y_test>el
    else:
        a=str(intervals[i-1])
        b=str(el)
        mask=np.logical_and(y_test<=el , y_test>intervals[i-1])

    print('For intervale ['+a+","+b+"] The error is :"+str(np.sum(np.abs(ypred[mask].round()-y_test[mask]))/len(y_test[mask])))
        

For intervale [0,5] The error is :0.637795725007848
For intervale [5,10] The error is :1.0000954745083064
For intervale [10,15] The error is :3.963531669865643
For intervale [+infini,15] The error is :15.051282051282051


In [125]:
da=pd.DataFrame([],columns=["level","mean error","median","q=0.75 error",'frequency'])
for i,el in enumerate(pd.Series(y_test).value_counts().index):
    mask=y_test==el
    da.loc[len(da)]=[el,np.sum(np.abs(ypred[mask].round()-y_test[mask]))/len(y_test[mask]),np.median(np.abs(ypred[mask].round()-y_test[mask])),np.quantile(np.abs(ypred[mask].round()-y_test[mask]),0.75),pd.Series(y_test).value_counts()[el]]

In [126]:
da.sort_values('mean error').head(20)

level  mean error  median  q=0.75 error  frequency
0     2.0    0.420292     0.0           1.0    12182.0
1     1.0    0.740494     0.0           1.0     7969.0
2     3.0    0.746459     1.0           1.0     5577.0
3     5.0    0.750806     1.0           1.0     4655.0
4     4.0    0.759716     1.0           1.0     4503.0
6     6.0    0.773270     1.0           1.0     3771.0
5     7.0    0.790444     1.0           1.0     4123.0
38   -1.0    1.000000     1.0           1.0        1.0
7     8.0    1.320269     1.0           2.0     1633.0
11    0.0    1.610390     1.0           2.0      154.0
8     9.0    2.058626     2.0           3.0      597.0
9    10.0    2.614286     2.0           4.0      350.0
10   11.0    3.188285     3.0           5.0      239.0
12   12.0    3.942308     4.0           5.0      104.0
13   13.0    4.432432     4.5           6.0       74.0
16   14.0    5.227273     5.5           7.0       44.0
15   15.0    5.583333     6.0           8.0       60.0
14   16.0    5.714286     5.0           8.0       63.0
17   18.0    6.704545     6.5          10.0       44.0
19   19.0    6.757576     6.0           9.0       33.0

In [ ]:
## erreur dans les batiments habités

In [185]:


print("number of buildings habitable ", np.where (pd.Series(list_encoders[0].inverse_transform(data_no.type_building.to_numpy().reshape(-1,1)).squeeze()).isin(["apartments","terrace","semidetached_house","residential","house","hotel","farm","dormitory","detached"]))[0].shape[0])

number of buildings habitable  141385


In [171]:
#les types des batiments dans X_test
types_buildings_test=list_encoders[0].inverse_transform(X_test.type_building.to_numpy().reshape(-1,1)).squeeze()

#mask pour les batiments habité
mask_habit=np.where (pd.Series(types_buildings_test).isin(["apartments","terrace","semidetached_house","residential","house","hotel","farm","dormitory","detached"]))[0]

In [181]:


print("median error pour les batiments habités :",np.median(np.abs(ypred[mask_habit].round()-y_test[mask_habit])))
print("moyenne error pour les batiments habités :",np.mean(np.abs(ypred[mask_habit].round()-y_test[mask_habit])))
print("0.75 quantile error pour les batiments habités :",np.quantile(np.abs(ypred[mask_habit].round()-y_test[mask_habit]),0.75))
print("std error pour les batiments habités :",np.std(np.abs(ypred[mask_habit].round()-y_test[mask_habit])))

median error pour les batiments habités : 0.0
moyenne error pour les batiments habités : 0.6622901955218055
0.75 quantile error pour les batiments habités : 1.0
std error pour les batiments habités : 1.1282510448339698


In [161]:
train_mask,test_mask=train_test_split(mask_habit,random_state=123,test_size=0.2)

### erreur dans paris

In [103]:
mask_paris=building_no_na.iloc[X_test.index].intersects(contour_iris[contour_iris['INSEE_COM'].apply(lambda x :x[0:2])=='75'].unary_union)

In [104]:
x_test_paris=X_test.loc[mask_paris.values]
y_test_paris=y_test[mask_paris.values]
dtest_paris=xgb.DMatrix(x_test_paris, label=y_test_paris)

In [105]:
print('n : ',len(x_test_paris))
print('The error is :'+str(np.sum(np.abs(model.predict(dtest_paris).round()-y_test_paris))/len(y_test_paris)))
print("Std test error:",np.std(np.abs(model.predict(dtest_paris).round()-y_test_paris)))
print("Median Abs error ",np.median(np.abs(model.predict(dtest_paris).round()-y_test_paris)))

n :  11770
The error is :1.0986406117247238
Std test error: 1.398156276241747
Median Abs error  1.0


### erreur dans IDF (sauf paris)

In [106]:
mask_idf=building_no_na.iloc[X_test.index].intersects(contour_iris[contour_iris['INSEE_COM'].apply(lambda x :x[0:2]).isin(['91',"92","93","94","95","77","78"])].unary_union)

In [107]:
x_test_idf=X_test.loc[mask_idf.values]
y_test_idf=y_test[mask_idf.values]
dtest_idf=xgb.DMatrix(x_test_idf, label=y_test_idf)

In [108]:
print('n : ',len(y_test_idf))
print('The error is :'+str(np.sum(np.abs(model.predict(dtest_idf).round()-y_test_idf))/len(y_test_idf)))
print("Std test error:",np.std(np.abs(model.predict(dtest_idf).round()-y_test_idf)))
print("Median Abs error ",np.median(np.abs(model.predict(dtest_idf).round()-y_test_idf)))

n :  10365
The error is :0.7766521948866377
Std test error: 1.3608809974993428
Median Abs error  0.0


### erreur dans les autres villes

In [67]:
indices_villes=np.setdiff1d(np.setdiff1d (X_test.index,x_test_idf.index),x_test_paris.index)
indices_villes

array([     9,     21,     22, ..., 192253, 192256, 192257], dtype=int64)

In [52]:
x_test_villes=X_test.iloc[np.where(X_test.index.isin( indices_villes))[0]]
y_test_villes=y_test[np.where(X_test.index.isin( indices_villes))[0]]
dtest_villes=xgb.DMatrix(x_test_villes, label=y_test_villes)

In [53]:
print('n : ',len(x_test_villes))
print('The error is :'+str(np.sum(np.abs(model.predict(dtest_villes).round()-y_test_villes))/len(y_test_villes)))
print("Std test error:",np.std(np.abs(model.predict(dtest_villes).round()-y_test_villes)))
print("Median Abs error ",np.median(np.abs(model.predict(dtest_villes).round()-y_test_villes)))

n :  24131
The error is :0.7312999875678587
Std test error: 1.2313125788165635
Median Abs error  0.0


### Train with all the data

In [109]:
ddata = xgb.DMatrix(data_no, label=building_level)
param = {'max_depth': 5, 'eta': 0.1, 'objective': 'reg:squarederror',"gamma":2,"lambda":4,"verbosity":0}
param['nthread'] = 4
param['eval_metric'] = ["mae"]
param['verbosity']=0

num_round = 500
start=time.time()
model = xgb.train(param, ddata, num_round)
### ADDD Other metrics STD and mediane absolute error
end=time.time()

print('The error is :'+str(np.sum(np.abs(model.predict(ddata).round()-building_level))/len(building_level)))
print("Std  error:",np.std(np.abs(model.predict(ddata).round()-building_level)))

print("Median Abs error ",np.median(np.abs(model.predict(ddata).round()-building_level)))
print('Train time '+str(end-start))

The error is :0.7312560520127265
Std  error: 1.0512993623579316
Median Abs error  0.0
Train time 147.86768770217896


In [113]:
pickle.dump(model, open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\modeles\\levels.pkl","wb"))

# Prediction des valeurs manquantes

In [25]:
building_na=all_building.loc[all_building.index.difference(building_no_na.index)]

In [26]:
iris_building_id_na=iris_building_id.reset_index("index_right").loc[building_na.index]
iris_building_id_na=iris_building_id_na.reset_index().set_index(['element_type',"osmid","index_right"])

In [27]:
iris_building_id_na=iris_building_id_na.reset_index("index_right")

In [28]:
def g(x):
    return list(zip(x['element_type'].values,x['osmid'].values))
iris_building_id['index_left']=[i for i in range(len(iris_building_id))]   
buildings_in_iris_=iris_building_id.reset_index().groupby("index_right").apply(lambda x:list(x['index_left'].values))

##buildings_in_iris_ == [iris , list of buildings]

In [29]:
keys_nearby_buildings=all_nearby_buildings.keys()
all_indices=[i for i in range(len(all_building))]

In [30]:
buildings_in_iris_index=buildings_in_iris_.index

In [31]:
keys_nearby_buildings=all_nearby_buildings.keys()

In [32]:
data_na=np.empty((len(building_na),45),dtype="object")

In [33]:
k=10
ids_batiments_voisins=np.empty((len(building_na),k),dtype="object")

In [21]:

#pour l'affichage
j=-1
err_buildings=[]

warnings.filterwarnings("ignore")
k=10

start_=time.time()
print('number of rows :'+str(len(building_na)))
for i ,row in building_na.iterrows():
    j+=1
    try:
        
        
        #used to display the execution time and other info and store intermediate data 
        if j%10000==0 and j!=0:
            print(round(100*j/len(building_na),2),"%")
            print("temps d'execution:",time.time()-start_)
            start_=time.time()
            pickle.dump(data_na,open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\\donnée_levels_na.pkl","wb"))
        
        
        #
        if i in  keys_nearby_buildings  and all_nearby_buildings[i][0] is not None:
            #iris of the current building
            current_iris_index=iris_building_id_na.loc[i]['index_right'].values[0]
    
            #iris nearby
            iris_ids=list(all_nearby_buildings[i])
            iris_ids.append(current_iris_index)
            iris_ids=list(buildings_in_iris_index.intersection(iris_ids))
            flat_list = [item for sublist in buildings_in_iris_.loc[iris_ids].values for item in sublist]
            '''#get all the indices of the buidlings in the nearby iris 
            mask=np.isin(np.array(iris_building_id.index.get_level_values("index_right")),iris_ids)

            #indices_=iris_building_id.iloc[mask].index
            indices=np.where(mask)[0]'''
            indices=flat_list
        else:
            print('####################################')
            #indices=building.index
            indices=buildings_in_iris_.loc[iris_building_id_na.loc[i]['index_right'].values[0]]
            
        #considerer que les batiment dont on connait leurs nombre d'étages
        #indices = building_no_na.index.intersection(indices)
        buildings_in_iris=all_building.iloc[indices]
        distance=buildings_in_iris.distance(row['geometry']).sort_values()
        #remove the current building from the distance dataframe (distance will be 0 ofc)
        try:
            distance=distance.drop(i)
        except:
            pass
        #take the k nearest neighboors
        #a=building_no_na.loc[distance.index].iloc[:k]
        a=buildings_in_iris.loc[distance.index].iloc[:k]
        
        ids_batiments_voisins[j]=a.index
        #buildings nearby
        areas=a.area.to_numpy()
        distances=distance.iloc[:k].to_numpy()
        types=a['building'].to_numpy()

        levels=np.vectorize (f )(a['building:levels'].to_numpy())

        #information about the iris
        iris=contour_iris.iloc[current_iris_index]


        if iris['TYP_IRIS'] ==iris['TYP_IRIS']:
            iris_type=np.array([iris['TYP_IRIS']])
        else:
            iris_type=None

        iris_area=np.array([iris['geometry'].area])

        #information about the building itself
        type_building=np.array([row['building']])
        area_building=np.array([row['geometry'].area])

        #densité 
        area=iris["geometry"].area/10**6
        iris=iris_data.loc[iris["CODE_IRIS"]]
        pop=iris['P17_POP']
        densite=[pop/area]

        
        if j%10000==0:s=time.time()
        data_na[j]=np.concatenate([type_building,area_building,iris_type,iris_area,densite,areas,types,levels,distances]).ravel()
     
        if j%10000==0:print(time.time()-s)
    except :
        print('error')
        err_buildings.append(i)


number of rows :6221923
0.0
0.16 %
temps d'execution: 412.8825342655182
0.0
####################################
####################################
####################################
####################################
0.32 %
temps d'execution: 410.27333664894104
0.0
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
0.48 %
temps d'execution: 360.7825999259949
0.0
0.64 %
temps d'execution: 250.31540250778198
0.0
0.8 %
temps d'execution: 328.2423577308655
0.0
0.96 %
temps d'execution: 302.01566886901855
0.0
1.13 %
temps d'execution: 258.4439971446991
0.0
1.29 %
temps d'execution: 337.003457546234

####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
15.27 %
temps d'execution: 291.9649443626404
0.0
15.43 %
temps d'execution: 235.1909408569336
0.0
15.59 %
temps d'execution: 374.4174768924713
0.0
15

0.0
38.25 %
temps d'execution: 510.1753897666931
0.0
38.41 %
temps d'execution: 404.93735432624817
0.0
38.57 %
temps d'execution: 462.57103538513184
0.0
38.73 %
temps d'execution: 645.2905223369598
0.0
38.89 %
temps d'execution: 382.1713869571686
0.0
39.06 %
temps d'execution: 426.65135288238525
0.0
####################################
39.22 %
temps d'execution: 440.57396388053894
0.0
39.38 %
temps d'execution: 461.6182222366333
0.0
39.54 %
temps d'execution: 345.45307445526123
0.0
39.7 %
temps d'execution: 355.6981256008148
0.0
39.86 %
temps d'execution: 443.94023036956787
0.0
####################################
40.02 %
temps d'execution: 528.6732468605042
0.0
40.18 %
temps d'execution: 347.23424458503723
0.0
40.34 %
temps d'execution: 452.13445591926575
0.0
40.5 %
temps d'execution: 392.9954152107239
0.0
40.66 %
temps d'execution: 491.93679642677307
0.0
40.82 %
temps d'execution: 509.06871795654297
0.0
40.98 %
temps d'execution: 417.6908142566681
0.0
41.14 %
temps d'execution: 525.9

0.010030746459960938
64.13 %
temps d'execution: 441.665714263916
0.0
64.29 %
temps d'execution: 428.06428265571594
0.0
64.45 %
temps d'execution: 442.90047240257263
0.0
64.61 %
temps d'execution: 478.9614577293396
0.0
64.77 %
temps d'execution: 376.516001701355
0.0
64.93 %
temps d'execution: 325.46630692481995
0.0
65.09 %
temps d'execution: 407.5883677005768
0.0
65.25 %
temps d'execution: 257.4017629623413
0.0
65.41 %
temps d'execution: 373.88147044181824
0.0
65.57 %
temps d'execution: 466.25242614746094
0.0
65.74 %
temps d'execution: 381.2211329936981
0.0
65.9 %
temps d'execution: 286.71301770210266
0.0
66.06 %
temps d'execution: 308.6297376155853
0.0
66.22 %
temps d'execution: 663.5833501815796
0.0
66.38 %
temps d'execution: 614.2827603816986
0.0
66.54 %
temps d'execution: 341.70776653289795
0.0
66.7 %
temps d'execution: 573.3304009437561
0.0
66.86 %
temps d'execution: 641.8780677318573
0.0
67.02 %
temps d'execution: 516.4254701137543
0.0
67.18 %
temps d'execution: 408.25263237953186

0.0
85.83 %
temps d'execution: 543.0952887535095
0.0
85.99 %
temps d'execution: 370.0565187931061
0.0
86.15 %
temps d'execution: 361.9603548049927
0.0
86.31 %
temps d'execution: 455.9396667480469
0.0
86.47 %
temps d'execution: 479.077449798584
0.0
86.63 %
temps d'execution: 601.6770708560944
0.0
86.79 %
temps d'execution: 462.6433048248291
0.0
86.95 %
temps d'execution: 493.0013995170593
0.0
87.11 %
temps d'execution: 516.681459903717
0.0
87.27 %
temps d'execution: 482.31768465042114
0.0
87.43 %
temps d'execution: 425.1001009941101
0.0
87.59 %
temps d'execution: 488.77718234062195
0.0
87.75 %
temps d'execution: 470.6395924091339
0.0
87.91 %
temps d'execution: 518.1183273792267
0.0
88.08 %
temps d'execution: 541.0069274902344
0.0
88.24 %
temps d'execution: 518.78204870224
0.0
####################################
####################################
####################################
####################################
####################################
#############################

####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
#

####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
93.7 %
temps d'execution: 527.8658289909363
0.0
####################################
####################################
###########################

0.0
95.15 %
temps d'execution: 480.6123652458191
0.0
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
######################

####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
####################################
#

In [26]:
data_na=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\données modele\\donnée_à_prédire_levels.pkl",'rb'))
#pickle.dump(data_na,open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\données modele\\donnée_à_prédire_levels.pkl",'wb'))
#pickle.dump(ids_batiments_voisins,open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\données modele\\ids_batiments_voisins_à_prédire_levels.pkl",'wb'))


In [27]:
#create a dataframe
columns=["type_building","area_building","iris_type","iris_area","iris_densite"]
for j in ["areas","types","levels","distances"]:
    for i in range(k):
        columns.append(j+str(i))

data_no_pred=pd.DataFrame(data_na,columns=columns)
data_no_pred.head()

type_building area_building iris_type      iris_area iris_densite  \
0  public_building   7101.313961         H    246197.6197   6638.56419   
1              yes   9391.609943         H  284455.046435  6985.026595   
2         hospital   6089.750617         H  384476.972915  4919.532057   
3       government  18298.845416         H  762106.637055   2761.82608   
4              yes  18838.431679         H  414825.303509  4693.361239   

        areas0       areas1       areas2       areas3        areas4  ...  \
0   555.933773    160.42465   356.639317   107.652029    1068.84441  ...   
1     91.13686    47.145037  3563.875794    563.11566   5301.464667  ...   
2  1579.332134  1136.468457    60.510863   273.667794  22313.407795  ...   
3   237.648816    67.316979   119.337701  1453.404804     187.60292  ...   
4  2496.020102  1134.987071  2131.757466   440.674566     86.271642  ...   

  distances0 distances1 distances2 distances3 distances4 distances5  \
0  13.908715  14.012931  14.118453  14.215182  14.330443  14.647469   
1  28.531324  29.259719  30.340425  30.370815  30.377087  47.162655   
2        0.0        0.0   8.875226  15.850351  22.056144  24.590759   
3        0.0    5.71293   6.996635  11.833926  12.835313  15.565037   
4        0.0        0.0   8.144574   9.149527  13.988666  17.601473   

  distances6 distances7 distances8 distances9  
0  14.745893  14.750351  14.864972  14.887084  
1  52.585452  56.810023  63.701802   64.08286  
2  31.557805  34.847719  50.548383  54.407739  
3  16.110759  16.639314    16.9769  17.203946  
4  20.470059  21.004165  21.882149  23.269902  

[5 rows x 45 columns]

In [29]:
del data_na
import gc 
gc.collect()

1188

In [28]:
#convert columns from object to int
for c in data_no_pred:
    if "area" in c or "levels" in c or "distances" in c or "iris_densite" in c:
        print(c)
        data_no_pred[c]=data_no_pred[c].astype(np.float32)

area_building
iris_area
iris_densite
areas0
areas1
areas2
areas3
areas4
areas5
areas6
areas7
areas8
areas9
levels0
levels1
levels2
levels3
levels4
levels5
levels6
levels7
levels8
levels9
distances0
distances1
distances2
distances3
distances4
distances5
distances6
distances7
distances8
distances9


In [38]:
i=0
for c in data_no_pred.columns:
    if data_no_pred[c].dtype=="O":
        print(c)
        
        enc=list_encoders[i]
        enc.set_params(encoded_missing_value=-1,handle_unknown="use_encoded_value")

        data_no_pred[c]=enc.transform(data_no_pred[c].to_numpy().reshape(-1,1) ).squeeze().astype(np.int)
        i+=1
        

type_building
iris_type
types0
types1
types2
types3
types4
types5
types6
types7
types8
types9


In [40]:
data_no_pred_matrix=xgb.DMatrix(data_no_pred)

In [41]:
model=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\modeles\\levels.pkl","rb"))
prediction=model.predict(data_no_pred_matrix).round()

In [43]:
#drop duplicated buildings
a=building_na[~building_na.index.duplicated(keep='first')]
b=prediction[~building_na.index.duplicated(keep='first')]

In [44]:
all_building=all_building[~all_building.index.duplicated(keep='first')]

In [45]:
all_building.loc[a.index,'building:levels']=b

In [46]:
for i ,row in list_departement.iterrows():
   
        contour_iris_dep=contour_iris
        #get the buidlings in teh departement
        try:
            building=pd.read_pickle(path+r"\\"+row["Département"].lower()+"_buildings.pkl").to_crs('EPSG:3857')
        except:
            continue
        
        
        #check duplicates
        if pd.Series(list(building.index)).value_counts().max()!=1:
            print('error:   there are duplicates .',pd.Series(list(building.index)).value_counts().max())
        
        
        #get the predictions
        m=np.where(all_building.index.isin(building.index))
        
        mm=all_building.iloc[m[0]]["building:levels"]
        building.loc[mm.index,"building:levels"]=mm
        
        pickle.dump(building,open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\osm filtre\batiments_levels\\"+row["Département"].lower()+"_buildings.pkl",'wb'))

   



## STATS

In [87]:
test_data=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\osm filtre\batiments_levels\\essonne_buildings.pkl",'rb'))

In [88]:
test_data['building:levels']=test_data['building:levels'].apply(f)

In [90]:
test_data[test_data.index.isin(building_na.index)].iloc[10000:20000].explore("building:levels")

In [52]:
for i ,row in list_departement.iterrows():
    try:
        contour_iris_dep=contour_iris
        #get the buidlings in teh departement
    
        building=pickle.load(open(r"Y:\RECHERCHE ET DEV\10_Modèle d'attractivite des rues\04_données clients (source)\osm filtre\batiments_levels\\"+row["Département"].lower()+"_buildings.pkl",'rb'))


        print(building_no_na[building_no_na.index.isin(building.index)]['building:levels'].apply(f).value_counts().head(5))
        print('\n\n')
    except:
        pass
   



2.0    10
3.0     3
1.0     3
4.0     1
8.0     1
Name: building:levels, dtype: int64



2.0    313
3.0    241
5.0    182
4.0    170
1.0     85
Name: building:levels, dtype: int64



2.0    887
3.0    489
1.0    455
4.0    452
5.0    433
Name: building:levels, dtype: int64



1.0    33
5.0    23
2.0    22
4.0    21
3.0    20
Name: building:levels, dtype: int64



4.0    1590
5.0    1386
2.0    1279
3.0     996
1.0     959
Name: building:levels, dtype: int64



2.0    419
1.0    294
3.0    236
4.0    153
5.0     76
Name: building:levels, dtype: int64



2.0    969
1.0    824
3.0    215
5.0    170
4.0    149
Name: building:levels, dtype: int64



2.0    96
3.0    51
1.0    49
4.0    19
5.0     4
Name: building:levels, dtype: int64



Series([], Name: building:levels, dtype: int64)



2.0    484
4.0    425
5.0    356
1.0    332
3.0    236
Name: building:levels, dtype: int64



2.0    3055
1.0    1735
3.0    1089
4.0     774
5.0     558
Name: building:levels, dtype: int64



2.0    1597
1.